In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime as dt
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import hvplot.pandas
import holoviews as hv
hv.extension('bokeh')

In [ ]:
df = pd.read_csv('data.csv', encoding = 'unicode_escape')
df.head()

InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

      InvoiceDate  UnitPrice  CustomerID         Country  
0  12/1/2010 8:26       2.55     17850.0  United Kingdom  
1  12/1/2010 8:26       3.39     17850.0  United Kingdom  
2  12/1/2010 8:26       2.75     17850.0  United Kingdom  
3  12/1/2010 8:26       3.39     17850.0  United Kingdom  
4  12/1/2010 8:26       3.39     17850.0  United Kingdom

In [ ]:
df.shape

(541909, 8)

In [ ]:
df.columns

Index(['InvoiceNo', 'StockCode', 'Description', 'Quantity', 'InvoiceDate',
       'UnitPrice', 'CustomerID', 'Country'],
      dtype='object')

In [ ]:
df.isnull().sum()

InvoiceNo           0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
UnitPrice           0
CustomerID     135080
Country             0
dtype: int64

In [ ]:
df.dtypes

InvoiceNo       object
StockCode       object
Description     object
Quantity         int64
InvoiceDate     object
UnitPrice      float64
CustomerID     float64
Country         object
dtype: object

In [ ]:
# pulling a df of just entries with customerIDs
custy_df = df[pd.notnull(df['CustomerID'])]

In [ ]:
custy_df = custy_df.copy()

In [ ]:
# Change InvoiceDate to datetime format
custy_df['InvoiceDate'] = pd.to_datetime(custy_df['InvoiceDate'])
# Change CustomerID to int
custy_df['CustomerID'] = custy_df['CustomerID'].astype('int')

In [ ]:
custy_df.dtypes

InvoiceNo              object
StockCode              object
Description            object
Quantity                int64
InvoiceDate    datetime64[ns]
UnitPrice             float64
CustomerID              int64
Country                object
dtype: object

In [ ]:
# create a column to see if teh price for the StockCode has changed and how much since the previous purchase
# custy_df['Price_Change'] = custy_df.groupby(['StockCode'])['UnitPrice'].diff()



In [ ]:
# get count of price changes
# custy_df['Price_Change'].value_counts()

In [ ]:
custy_df['CustomerID'].value_counts()

17841    7983
14911    5903
14096    5128
12748    4642
14606    2782
         ... 
15070       1
15753       1
17065       1
16881       1
16995       1
Name: CustomerID, Length: 4372, dtype: int64

### Kmeans Customer Segmentation

In [ ]:
# scale the data for clustering
scaler = StandardScaler()
custy_df_scaled = scaler.fit_transform(custy_df[['Quantity', 'UnitPrice']])
k_custy_df_scaled = pd.DataFrame(custy_df_scaled, columns=['Quantity', 'UnitPrice'])

# Add the CustomerID back in
k_custy_df_scaled['CustomerID'] = custy_df['CustomerID']

k_custy_df_scaled.head()

Quantity  UnitPrice  CustomerID
0 -0.024373  -0.013135     17850.0
1 -0.024373  -0.001017     17850.0
2 -0.016331  -0.010250     17850.0
3 -0.024373  -0.001017     17850.0
4 -0.024373  -0.001017     17850.0

In [ ]:
# drop customerIDs with any letter in them
# k_custy_df_scaled2 = k_custy_df_scaled[k_custy_df_scaled['CustomerID'].astype(str).str.isdigit()]
# k_custy_df_scaled2.head()

In [ ]:
# drop CustomerID C536379
k_custy_df_scaled2 = k_custy_df_scaled[k_custy_df_scaled['CustomerID'] != 'C536379']


In [ ]:
k_custy_df_scaled2['CustomerID'] = pd.to_numeric(k_custy_df_scaled2['CustomerID'], errors='coerce')


In [ ]:
k_custy_df_scaled2.isnull().sum()

# drop NaNs
k_custy_df_scaled3 = k_custy_df_scaled2.dropna()

In [ ]:
k_custy_df_scaled3.dtypes

Quantity      float64
UnitPrice     float64
CustomerID    float64
dtype: object

In [ ]:
# elbow method to find optimal number of clusters
# Create a a list to store inertia values
inertia = []

# Create a a list to store the values of k
k = list(range(1, 11))

# Create a for-loop where each value of k is evaluated using the K-means algorithm
# Fit the model using the spread_df DataFrame
# Append the value of the computed inertia from the `inertia_` attribute of the KMeans model instance

for i in k:
    km = KMeans(n_clusters=i, random_state=1, n_init='auto')
    km.fit(k_custy_df_scaled3)
    inertia.append(km.inertia_)

# Create a dictionary with the data to plot the Elbow curve
elbow_data = {"k": k, "inertia": inertia}

# Create a DataFrame with the data to plot the Elbow curve
df_elbow = pd.DataFrame(elbow_data)

df_elbow.head()

k       inertia
0  1  8.936285e+11
1  2  2.279566e+11
2  3  9.743627e+10
3  4  5.349757e+10
4  5  3.376651e+10

In [ ]:
# Plot a line chart with the data to explore the Elbow curve
df_elbow.hvplot.line(x="k", y="inertia", title="Elbow Curve", xticks=k)


:Curve   [k]   (inertia)

In [ ]:
k_custy_df_scaled4 = k_custy_df_scaled3.copy()

In [ ]:
# Create a kmeans model with k=3
kmeans = KMeans(n_clusters=3, random_state=1, n_init='auto')

kmeans.fit(k_custy_df_scaled4)

kmeans.cluster_centers_

kmeans.labels_

k_custy_df_scaled4['cluster'] = kmeans.labels_

k_custy_df_scaled4.head()

Quantity  UnitPrice  CustomerID  cluster
0 -0.024373  -0.013135     17850.0        1
1 -0.024373  -0.001017     17850.0        1
2 -0.016331  -0.010250     17850.0        1
3 -0.024373  -0.001017     17850.0        1
4 -0.024373  -0.001017     17850.0        1

In [ ]:
k_custy_df_scaled4['cluster'].value_counts()

2    112144
1    105371
0     85180
Name: cluster, dtype: int64

In [ ]:
k_custy_df_scaled4['CustomerID'].value_counts()

17841.0    5660
14911.0    4388
12748.0    2544
14606.0    2316
15311.0    2090
           ... 
18113.0       1
16323.0       1
13135.0       1
13270.0       1
13391.0       1
Name: CustomerID, Length: 3875, dtype: int64

In [ ]:
# plot the clusters using hvplot
k_custy_df_scaled4.hvplot.scatter(x='Quantity', y='UnitPrice', by='cluster')



:NdOverlay   [cluster]
   :Scatter   [Quantity]   (UnitPrice)

### Bringing cluster back to the main df

In [ ]:
# add the cluster column to the original df
custy_df['cluster'] = k_custy_df_scaled4['cluster']


In [ ]:
custy_df['cluster'].value_counts()

2.0    112144
1.0    105371
0.0     85180
Name: cluster, dtype: int64

In [ ]:
custy_df.head()

InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice  CustomerID         Country  cluster  
0 2010-12-01 08:26:00       2.55       17850  United Kingdom      1.0  
1 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0  
2 2010-12-01 08:26:00       2.75       17850  United Kingdom      1.0  
3 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0  
4 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0

In [ ]:
# Group the data by the cluster column and compute summary statistics
cluster_stats = custy_df.groupby('cluster').agg({'Quantity': ['mean', 'median', 'std'],
                                                 'UnitPrice': ['mean', 'median', 'std', 'sum']})

# Round the summary statistics
cluster_stats = cluster_stats.round(2)

# Rename the columns to make them easier to read
cluster_stats.columns = ['Qty Mean', 'Qty Median', 'Qty Std', 'Price Mean', 'Price Median', 'Price Std', 'Total Sales']

# Print the summary statistics
print(cluster_stats)

         Qty Mean  Qty Median  Qty Std  Price Mean  Price Median  Price Std  \
cluster                                                                       
0.0         14.11         8.0   362.22        3.73          1.95      32.18   
1.0         12.08         4.0    48.64        3.11          1.95      20.67   
2.0         11.77         4.0    51.85        3.91          1.95     124.90   

         Total Sales  
cluster               
0.0        317662.87  
1.0        328103.88  
2.0        439000.08  


Cluster 0: This cluster has a higher mean and median Quantity compared to the other clusters, and a higher standard deviation of Quantity compared to cluster 1. This suggests that customers in this segment tend to purchase larger quantities of items, but with a greater variation in the number of items purchased. The mean UnitPrice for this cluster is similar to the other clusters, with a slightly lower median UnitPrice and a higher standard deviation of UnitPrice compared to cluster 1.

Cluster 1: This cluster has a lower mean and median Quantity compared to cluster 0, but with a lower standard deviation of Quantity compared to cluster 0. This suggests that customers in this segment tend to purchase smaller quantities of items, with less variation in the number of items purchased. The mean UnitPrice for this cluster is similar to the other clusters, with a slightly higher median UnitPrice and a lower standard deviation of UnitPrice compared to cluster 0.

Cluster 2: This cluster has a similar mean and median Quantity compared to the other clusters, but with a higher standard deviation of Quantity compared to cluster 1. This suggests that customers in this segment tend to purchase similar quantities of items as the other clusters, but with a greater variation in the number of items purchased. The mean and median UnitPrice for this cluster are higher compared to the other clusters, and the standard deviation of UnitPrice is also higher compared to cluster 3.

Cluster 3: This cluster has a similar mean and median Quantity compared to the other clusters, but with a lower standard deviation of Quantity compared to cluster 1. This suggests that customers in this segment tend to purchase similar quantities of items as the other clusters, but with a lesser variation in the number of items purchased. The mean UnitPrice for this cluster is similar to the other clusters, with a lower median UnitPrice and a lower standard deviation of UnitPrice compared to cluster 2.


next steps could include conducting further analysis on customer behavior and preferences within each cluster to gain deeper insights into their purchasing habits. This could include analyzing the timing of purchases, purchase frequency, product categories, and other relevant factors. You could also use this information to develop targeted marketing strategies or promotions to increase sales and customer loyalty.

In [ ]:
print (f'The earliest date in the dataset is {custy_df["InvoiceDate"].min()}')
print (f'The latest date in the dataset is {custy_df["InvoiceDate"].max()}')



The earliest date in the dataset is 2010-12-01 08:26:00
The latest date in the dataset is 2011-12-09 12:50:00


In [ ]:
custy_df.head()

InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice  CustomerID         Country  cluster  
0 2010-12-01 08:26:00       2.55       17850  United Kingdom      1.0  
1 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0  
2 2010-12-01 08:26:00       2.75       17850  United Kingdom      1.0  
3 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0  
4 2010-12-01 08:26:00       3.39       17850  United Kingdom      1.0

In [ ]:
# sales by country by cluster
sales_by_country_cluster = custy_df.groupby(['Country', 'cluster'])['UnitPrice'].sum().reset_index()

# Create the stacked bar chart
stacked_bar = sales_by_country_cluster.hvplot.bar(x='Country', y='UnitPrice', by='cluster', stacked=True, rot=90, title='Total Sales by Country and Cluster')

# Display the plot
stacked_bar


:Bars   [Country,cluster]   (UnitPrice)

In [ ]:
# Line graph of daily sales by cluster
daily_sales_by_cluster = custy_df.groupby(['InvoiceDate', 'cluster'])['UnitPrice'].sum().reset_index()
daily_sales_by_cluster.hvplot.line(x='InvoiceDate', y='UnitPrice', by='cluster', xlabel='Date', ylabel='Total Sales', title='Daily Sales by Cluster')



:NdOverlay   [cluster]
   :Curve   [InvoiceDate]   (UnitPrice)

In [ ]:
# stacked bar graph of sales by cluster by month
custy_df['Month'] = custy_df['InvoiceDate'].dt.month
monthly_sales_by_cluster = custy_df.groupby(['Month', 'cluster'])['UnitPrice'].sum().reset_index()
# monthly_sales_by_cluster.hvplot.bar(x='Month', y='UnitPrice', by='cluster', stacked=True, rot=90, title='Monthly Sales by Cluster')
monthly_sales_by_cluster.hvplot.bar(x='Month', y='UnitPrice', by='cluster', stacked=True, rot=90, title='Monthly Sales by Cluster', xlabel='Month', ylabel='Total Sales')

:Bars   [Month,cluster]   (UnitPrice)

In [ ]:
#Scatter plot of quantity and unit price by cluster:
# scatter_data = custy_df[['Quantity', 'UnitPrice', 'cluster']]
# scatter_data.hvplot.scatter(x='Quantity', y='UnitPrice', by='cluster', title='Quantity and UnitPrice by Cluster')

In [ ]:
# Heatmap of sales by month and product category
